# "Density" statistics & density plot

 Statistics "density" are calculated on the sample of a single continuous variable; It approximates the Probability Density Function (PDF) of this sample. "Density" statistic samples this function points. 
 It's weighted; it means the counted density depends on observation weights.

This notebook uses definitions from [DataFrame](https://kotlin.github.io/dataframe/overview.html).

## Usage

"Density" statistic is useful when you have a large dataset, and you want to understand the underlying probability distribution. Density plot visualizes the PDF and also allows you to compare the distribution of different samples. This is a useful alternative to the histogram for continuous data that comes from an underlying smooth distribution.

## Arguments

* Input (mandatory):
  - `x` - numeric sample on which the statistics are calculated;
* Weights (optional):
  - `weights` - set of weights of the same size as the input sample; `null` (by default) means all weights are equal to `1.0` and the weighted density is equal to the normal one;
* Parameters (optional):
  - `n: Int` - number of sampled points;
  - `trim: Boolean` - if `false`, each density is computed on the full range of the data; if `true`, each density is computed over the range of that group (only for grouped inputs).
  - `adjust: Double` - adjusts the value of bandwidth by multiplying it; changes how smooth the frequency curve is. 
  - `kernel: Kernel` - the kernel used to calculate the density function:
    - `Kernel.GAUSSIAN`
    - `Kernel.RECTANGULAR`
    - `Kernel.TRIANGULAR`
    - `Kernel.BIWEIGHT` 
    - `Kernel.EPANECHNIKOV`
    - `Kernel.OPTCOSINE`  
  - `fullScanMax: Int` - maximum size of data to use density computation with 'full scan'; for bigger data, less accurate but more efficient density computation is applied;
  - `bandWidth: BandWidth` - the method (or exact value) of bandwidth:
    - `BandWidth.Method.NRD`
    - `BandWidth.Method.NRD0`
    - `BandWidth.value(value: Double)`  

### Generalized signature

The specific signature depends on the function, but all functions related to "density" statistic (which will be discussed further below - different variations of `statDnesity()`, `densityPlot()`) have approximately the same signature with the arguments above:

```
statCountArgs := 
   x, 
   weights = null,
   n: Int = 512,
   trim: Boolean = false,
   adjust: Double = 1.0,
   kernel: Kernel = Kernel.GAUSSIAN,
   fullScanMax: Int = 5000,
   bandWidth: BandWidth = BandWidth.Method.NRD0,
```

The possible types of `x` and `weights` depend on where a certain function is used. They can be simply `Iterable` (`List`, `Set`, etc.) or a reference to a column in a `DataFrame` (`String`, `ColumnAccessor`) or the `DataColumn` itself.

## Output statistics

| name                 | type   | description                                 |
|----------------------|--------|---------------------------------------------|
| Stat.x               | Double | `x` coordinate                              |
| Stat.density         | Double | Density estimate                            |
| Stat.densityWeighted | Double | Weighted density                            |
| Stat.scaled          | Double | Density estimate, scaled to maximin of 1.0. |
| Stat.scaledWeighted  | Double | Weighted scaled                             |

## StatDensity plots

In [1]:
%use dataframe(0.11.1)
%use kandy(0.4.5-dev-29)
@file:Repository("https://packages.jetbrains.team/maven/p/kds/kotlin-ds-maven")
@file:DependsOn("org.jetbrains.kotlinx:kotlin-statistics-jvm:0.0.0-dev-10")

In [2]:
// to generate the data we use a standard java math library
// https://commons.apache.org/proper/commons-math/
import org.apache.commons.math3.distribution.NormalDistribution
import org.apache.commons.math3.distribution.UniformRealDistribution

// generate sample from normal distribution
val depthList = NormalDistribution(500.0, 100.0).sample(1000).toList()
// generate sample from uniform distribution
val coeffList = UniformRealDistribution(0.0, 1.0).sample(1000).toList()

In [3]:
// gather them into the DataFrame
val df = dataFrameOf(
    "depth" to depthList,
    "coeff" to coeffList
)

In [4]:
df.head(5)

<iframe onload="o_resize_iframe_out_1()" style="width:100%;" class="result_container" id="iframe_out_1" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-385875968"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i

`df` has a signature

<table>
  <thead>
    <tr>
      <th>depth</th>
      <th>coeff</th>
    </tr>
  </thead>
</table>

Let's take a look at `StatDensity` output DataFrame:

In [5]:
df.statDensity("depth", "coeff").head(5)

<iframe onload="o_resize_iframe_out_2()" style="width:100%;" class="result_container" id="iframe_out_2" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-385875967"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 1</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i

It has the following signature:

<table>
  <thead>
    <tr>
      <th alignt="left" colspan="5">Stat</th>
    </tr>
  </thead>
  <thead>
    <tr>
      <th>x</th>
      <th>density</th>
      <th>densityWeighted</th>
      <th>scaled</th>
      <th>scaledWeighted</th>
    </tr>
  </thead>
</table>

As you can see, we got a `DataFrame` with one `ColumnGroup` called `Stat` which contains several columns with statics. For `statDensity`, each row corresponds to one PDF points. `Stat.x` is the column with this point `x` coordinate; `Stat.density` contains the estimated density; `Stat.densityWeighted` - weighted version of `density`; `Stat.scaled` is a density scaled to maximin of 1.0; `Stat.scaledWeighted` - weighted version of `scaled`.
`DataFrame` with "density" statistics is called `StatDesnityFrame`

### `statDensity` transform

`statDensity(statDensityArgs) { /*new plotting context*/ }` modifies a plotting context - instead of original data (no matter was it empty or not) new `StatDensity` dataset (calculated on given arguments; inputs and weights can be provided as `Iterable` or as dataset column reference - by name as a `String`, as a `ColumnReference` or as a `DataColumn`) is used inside a new context (original dataset and primary context are not affected - you can add layers using initial dataset outside the `statDensity` context). Since the old dataset is irrelevant, we cannot use references for its columns. But we can refer to the new ones. They are all contained in the `Stat` group and can be called inside the new context:

In [6]:
plot {
    statDensity(depthList, adjust = 0.2) {
        // new `StatDensity` dataset here
        line {
            // use `Stat.*` columns for mappings
            x(Stat.x)
            y(Stat.density)
            color(Stat.density)
        }
    }
} 

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 0.0040
 
 
 
 
 
 
 0.0045
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 density
 
 
 
 
 x
 
 
 
 
 
 
 
 
 density
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 
 
 0.004

### DensityPlot layer

Density plot is a statistical plot used for visualizing the distribution of continuous variable. It's an area graph of kernel estimated PDF. So basically, we can build a histogram with `statDensity` as follows:

In [7]:
val statDesnityAndAreaPlot = df.plot {
    statDensity("depth") {
        area {
            x(Stat.x)
            y(Stat.density)
        }
    }
    layout.title = "`statDensity()` + `area()` layer"
}
statDesnityAndAreaPlot

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M23.455612836968818 318.1393964319663 L23.455612836968818 318.1393964319663 L24.3736407366545 318.07928312770616 L25.291668636340155 318.0177499901063 L26.209696536025824 317.95437937038514 L27.127724435711492 317.888723425447 L28.04575233539716 317.82031213226344 L28.963780235082844 317.74866232705443 L29.881808134768498 317.6732876063912 L30.799836034454167 317.5937088977619 L31.717863934139835 317.5094654815489 L32.635891833825504 317.4201262256385 L33.55391973351117 317.32530077876817 L34.47194763319684 317.2246504598187 L35.38997553288251 317.1178985780236 L36.30800343256818 317.0048399237426 L37.22603133225385 316.8853491810948 L38.144059231939515 316.759388032223 L39.06208713162517 316.6270107479244 L39.98011503131084 316.4883680902838 L40.89814293099652 316.34370938907466 L41.81617083068219 316.1933826941445 L42.73419873036786 316.03783294976284 L43.65222663005351 315.8775981828176 L44.57025452973918 315.7133037435866 L45.48828242942486 315.5456546843058 L46.40631032911053 315.37542640561657 L47.32433822879619 315.20345374295437 L48.242366128481855 315.03061870284415 L49.160394028167524 314.8578370918181 L50.07842192785319 314.68604430732177 L50.996449827538875 314.516180579757 L51.91447772722454 314.3491759671504 L52.8325056269102 314.1859354084828 L53.750533526595866 314.02732413835116 L54.668561426281535 313.8741537544781 L55.58658932596719 313.72716921100266 L56.50461722565287 313.58703698506895 L57.42264512533854 313.4543346327821 L58.34067302502421 313.32954191412216 L59.25870092470988 313.21303362603237 L60.176728824395546 313.1050742399098 L61.0947567240812 313.00581439544294 L62.01278462376688 312.91528925854055 L62.93081252345255 312.833418708311 L63.84884042313822 312.7600092779576 L64.76686832282388 312.6947577382076 L65.68489622250954 312.6372561804929 L66.60292412219522 312.58699843135423 L67.5209520218809 312.54338761004067 L68.43897992156656 312.50574462836806 L69.35700782125224 312.47331742568446 L70.2750357209379 312.44529073212226 L71.19306362062355 312.42079615979816 L72.11109152030923 312.39892243365057 L73.02911941999488 312.37872559037214 L73.94714731968057 312.35923899444094 L74.86517521936622 312.33948304350236 L75.7832031190519 312.3184744601516 L76.70123101873759 312.2952350923473 L77.61925891842324 312.26880016909786 L78.53728681810892 312.23822598063543 L79.45531471779455 312.2025969720719 L80.37334261748023 312.16103225571334 L81.29137051716589 312.1126915591948 L82.20939841685157 312.05678063397806 L83.12742631653722 311.99255615138674 L84.04545421622291 311.91933011129504 L84.96348211590859 311.83647378217427 L85.88151001559424 311.74342118095774 L86.79953791527993 311.63967208787807 L87.71756581496558 311.5247945759721 L88.63559371465124 311.3984270184116 L89.55362161433692 311.260279520363 L90.47164951402257 311.1101347069135 L91.38967741370826 310.94784778593055 L92.30770531339391 310.7733457956856 L93.2257332130796 310.58662594271044 L94.14376111276525 310.3877529365107 L95.06178901245093 310.17685523510374 L95.97981691213661 309.95412012925397 L96.89784481182227 309.7197876138595 L97.81587271150792 309.4741430219875 L98.73390061119358 309.21750843003576 L99.65192851087926 308.95023288056075 L100.56995641056491 308.67268151130907 L101.4879843102506 308.3852237234905 L102.40601220993628 308.0882205676863 L103.32404010962193 307.78201157016366 L104.24206800930762 307.4669012638423 L105.16009590899327 307.14314572476303 L106.07812380867892 306.8109394447458 L106.99615170836461 306.4704028922167 L107.91417960805026 306.1215711243939 L108.83220750773594 305.7643838138977 L109.7502354074216 305.3986770405169 L110.66

But we can do it even faster with `densityPlot(statDensityArgs)` method:

In [8]:
val densityPlotLayerPlot = plot {
    densityPlot(depthList)
    layout.title = "`densityPlot()` layer"
}
densityPlotLayerPlot

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M23.455612836968818 318.1393964319663 L23.455612836968818 318.1393964319663 L24.3736407366545 318.07928312770616 L25.291668636340155 318.0177499901063 L26.209696536025824 317.95437937038514 L27.127724435711492 317.888723425447 L28.04575233539716 317.82031213226344 L28.963780235082844 317.74866232705443 L29.881808134768498 317.6732876063912 L30.799836034454167 317.5937088977619 L31.717863934139835 317.5094654815489 L32.635891833825504 317.4201262256385 L33.55391973351117 317.32530077876817 L34.47194763319684 317.2246504598187 L35.38997553288251 317.1178985780236 L36.30800343256818 317.0048399237426 L37.22603133225385 316.8853491810948 L38.144059231939515 316.759388032223 L39.06208713162517 316.6270107479244 L39.98011503131084 316.4883680902838 L40.89814293099652 316.34370938907466 L41.81617083068219 316.1933826941445 L42.73419873036786 316.03783294976284 L43.65222663005351 315.8775981828176 L44.57025452973918 315.7133037435866 L45.48828242942486 315.5456546843058 L46.40631032911053 315.37542640561657 L47.32433822879619 315.20345374295437 L48.242366128481855 315.03061870284415 L49.160394028167524 314.8578370918181 L50.07842192785319 314.68604430732177 L50.996449827538875 314.516180579757 L51.91447772722454 314.3491759671504 L52.8325056269102 314.1859354084828 L53.750533526595866 314.02732413835116 L54.668561426281535 313.8741537544781 L55.58658932596719 313.72716921100266 L56.50461722565287 313.58703698506895 L57.42264512533854 313.4543346327821 L58.34067302502421 313.32954191412216 L59.25870092470988 313.21303362603237 L60.176728824395546 313.1050742399098 L61.0947567240812 313.00581439544294 L62.01278462376688 312.91528925854055 L62.93081252345255 312.833418708311 L63.84884042313822 312.7600092779576 L64.76686832282388 312.6947577382076 L65.68489622250954 312.6372561804929 L66.60292412219522 312.58699843135423 L67.5209520218809 312.54338761004067 L68.43897992156656 312.50574462836806 L69.35700782125224 312.47331742568446 L70.2750357209379 312.44529073212226 L71.19306362062355 312.42079615979816 L72.11109152030923 312.39892243365057 L73.02911941999488 312.37872559037214 L73.94714731968057 312.35923899444094 L74.86517521936622 312.33948304350236 L75.7832031190519 312.3184744601516 L76.70123101873759 312.2952350923473 L77.61925891842324 312.26880016909786 L78.53728681810892 312.23822598063543 L79.45531471779455 312.2025969720719 L80.37334261748023 312.16103225571334 L81.29137051716589 312.1126915591948 L82.20939841685157 312.05678063397806 L83.12742631653722 311.99255615138674 L84.04545421622291 311.91933011129504 L84.96348211590859 311.83647378217427 L85.88151001559424 311.74342118095774 L86.79953791527993 311.63967208787807 L87.71756581496558 311.5247945759721 L88.63559371465124 311.3984270184116 L89.55362161433692 311.260279520363 L90.47164951402257 311.1101347069135 L91.38967741370826 310.94784778593055 L92.30770531339391 310.7733457956856 L93.2257332130796 310.58662594271044 L94.14376111276525 310.3877529365107 L95.06178901245093 310.17685523510374 L95.97981691213661 309.95412012925397 L96.89784481182227 309.7197876138595 L97.81587271150792 309.4741430219875 L98.73390061119358 309.21750843003576 L99.65192851087926 308.95023288056075 L100.56995641056491 308.67268151130907 L101.4879843102506 308.3852237234905 L102.40601220993628 308.0882205676863 L103.32404010962193 307.78201157016366 L104.24206800930762 307.4669012638423 L105.16009590899327 307.14314572476303 L106.07812380867892 306.8109394447458 L106.99615170836461 306.4704028922167 L107.91417960805026 306.1215711243939 L108.83220750773594 305.7643838138977 L109.7502354074216 305.3986770405169 L110.66

Let's compare them:

In [9]:
plotGrid(listOf(statDesnityAndAreaPlot, densityPlotLayerPlot))

200
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M16.54652192787791 318.1393964319663 L16.54652192787791 318.1393964319663 L17.194135310573728 318.07928312770616 L17.84174869326953 318.0177499901063 L18.48936207596534 317.95437937038514 L19.136975458661148 317.888723425447 L19.784588841356957 317.82031213226344 L20.432202224052766 317.74866232705443 L21.079815606748575 317.6732876063912 L21.727428989444384 317.5937088977619 L22.375042372140186 317.5094654815489 L23.022655754836002 317.4201262256385 L23.670269137531804 317.32530077876817 L24.317882520227613 317.2246504598187 L24.965495902923422 317.1178985780236 L25.61310928561923 317.0048399237426 L26.26072266831504 316.8853491810948 L26.90833605101085 316.759388032223 L27.55594943370665 316.6270107479244 L28.20356281640246 316.4883680902838 L28.851176199098276 316.34370938907466 L29.498789581794078 316.1933826941445 L30.1464029644899 316.03783294976284 L30.794016347185696 315.8775981828176 L31.441629729881505 315.7133037435866 L32.089243112577314 315.5456546843058 L32.73685649527312 315.37542640561657 L33.38446987796892 315.20345374295437 L34.03208326066474 315.03061870284415 L34.67969664336055 314.8578370918181 L35.32731002605636 314.68604430732177 L35.97492340875217 314.516180579757 L36.62253679144798 314.3491759671504 L37.27015017414377 314.1859354084828 L37.917763556839596 314.02732413835116 L38.565376939535405 313.8741537544781 L39.2129903222312 313.72716921100266 L39.86060370492701 313.58703698506895 L40.50821708762282 313.4543346327821 L41.15583047031863 313.32954191412216 L41.80344385301445 313.21303362603237 L42.45105723571026 313.1050742399098 L43.098670618406054 313.00581439544294 L43.74628400110186 312.91528925854055 L44.39389738379767 312.833418708311 L45.04151076649348 312.7600092779576 L45.68912414918929 312.6947577382076 L46.3367375318851 312.6372561804929 L46.98435091458091 312.58699843135423 L47.63196429727672 312.54338761004067 L48.279577679972526 312.50574462836806 L48.927191062668335 312.47331742568446 L49.574804445364144 312.44529073212226 L50.22241782805995 312.42079615979816 L50.87003121075576 312.39892243365057 L51.51764459345156 312.37872559037214 L52.165257976147366 312.35923899444094 L52.812871358843175 312.33948304350236 L53.460484741539 312.3184744601516 L54.10809812423481 312.2952350923473 L54.755711506930616 312.26880016909786 L55.403324889626425 312.23822598063543 L56.05093827232222 312.2025969720719 L56.69855165501803 312.16103225571334 L57.34616503771384 312.1126915591948 L57.99377842040965 312.05678063397806 L58.641391803105456 311.99255615138674 L59.289005185801265 311.91933011129504 L59.936618568497074 311.83647378217427 L60.58423195119288 311.74342118095774 L61.23184533388871 311.63967208787807 L61.8794587165845 311.5247945759721 L62.52707209928031 311.3984270184116 L63.17468548197612 311.260279520363 L63.822298864671914 311.1101347069135 L64.46991224736772 310.94784778593055 L65.11752563006354 310.7733457956856 L65.76513901275936 310.58662594271044 L66.41275239545516 310.3877529365107 L67.06036577815098 310.17685523510374 L67.70797916084678 309.95412012925397 L68.35559254354257 309.7197876138595 L69.0032059262384 309.4741430219875 L69.65081930893419 309.21750843003576 L70.29843269163001 308.95023288056075 L70.9460460743258 308.67268151130907 L71.59365945702163 308.3852237234905 L72.24127283971742 308.0882205676863 L72.88888622241325 307.78201157016366 L73.53649960510907 307.4669012638423 L74.18411298780487 307.14314572476303 L74.83172637050066 306.8109394447458 L75.47933975319648 306.4704028922167 L76.12695313589228 306.1215711243939 L76.7745665185881 305.7643838138977 L77.4221799012839 305.3986770405169 L78.06979328397972 305.0241771738705 L78.71740666667552 304.6404971350706 L79.365020049371

These two plots are identical. Indeed, `densityPlot` just uses `statDensity` and `area` and performs coordinates mappings under the hood. And of course we can customize `densityPlot` layer: `densityPlot()` optionally opens a new context, where we can configure bars (as in usual context opened by `area { ... }`) - even change coordinate mappings from default ones. `StatDensity` dataset of `densityPlot` is also can be accessed here.

In [10]:
df.plot {
    densityPlot(depth) {
         // change a column mapped on `y` to `Stat.scaled`
        y(Stat.scaled)
        alpha = 0.7
        fillColor = Color.RED
        borderLine.color = Color.BLACK
    }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0
 
 
 
 
 
 
 0.2
 
 
 
 
 
 
 0.4
 
 
 
 
 
 
 0.6
 
 
 
 
 
 
 0.8
 
 
 
 
 
 
 1.0
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M24.543877217259954 341.9998511643638 L24.543877217259954 341.9998511643638 L25.504498634765234 341.93522936228413 L26.465120052270514 341.86908123936433 L27.425741469775794 341.800957823164 L28.386362887281074 341.7303776823555 L29.346984304786353 341.6568355421832 L30.307605722291648 341.57981200158355 L31.268227139796913 341.4987841768706 L32.22884855730221 341.4132370650941 L33.18946997480747 341.3226753926651 L34.15009139231277 341.2266356925614 L35.11071280981803 341.1246983371758 L36.07133422732333 341.0164992443051 L37.03195564482861 340.9017409713754 L37.992577062333886 340.78020291802335 L38.953198479839166 340.6517503696769 L39.91381989734446 340.51634213463973 L40.874441314849726 340.3740365540187 L41.835062732355006 340.22499569705514 L42.795684149860286 340.06948759325525 L43.75630556736558 339.9078863962053 L44.71692698487086 339.74067042099506 L45.677548402376125 339.5684180465289 L46.63816981988142 339.3918015243556 L47.5987912373867 339.2115787856287 L48.55941265489198 339.0285833860378 L49.520034072397245 338.843712773676 L50.48065548990254 338.6579151055575 L51.44127690740782 338.47217487370443 L52.40189832491311 338.28749763037086 L53.36251974241839 338.1048941232388 L54.32314115992367 337.9253641646867 L55.28376257742894 337.74988056411905 L56.24438399493423 337.5793734487275 L57.20500541243951 337.41471528606394 L58.16562682994478 337.2567069018279 L59.12624824745007 337.1060647589491 L60.08686966495535 336.96340973024076 L61.04749108246063 336.82925755768133 L62.008112499965925 336.70401114798483 L62.968733917471205 336.58795480790303 L63.92935533497647 336.4812504751012 L64.88997675248177 336.3839359529311 L65.85059816998705 336.2959251114343 L66.81121958749233 336.2170099738044 L67.77184100499758 336.14686456857316 L68.73246242250289 336.08505039402985 L69.69308384000817 336.03102331370576 L70.65370525751345 335.98414168079375 L71.61432667501873 335.94367547549564 L72.57494809252401 335.9088162326108 L73.53556951002929 335.87868753703145 L74.49619092753457 335.852355871783 L75.45681234503985 335.8288416161744 L76.41743376254513 335.80713000965005 L77.37805518005041 335.78618191902405 L78.33867659755569 335.76494427176505 L79.29929801506097 335.742360044663 L80.25991943256625 335.7173777242734 L81.22054085007156 335.6889601817802 L82.18116226757684 335.6560929291831 L83.14178368508209 335.61779174497724 L84.10240510258737 335.57310967489184 L85.06302652009265 335.52114342613436 L86.02364793759793 335.4610391815264 L86.98426935510321 335.3919978627407 L87.94489077260852 335.31327986964214 L88.9055121901138 335.22420931583736 L89.86613360761908 335.1241777695296 L90.82675502512436 335.0126474944689 L91.78737644262964 334.88915416917 L92.74799786013492 334.75330904479245 L93.7086192776402 334.6048004843902 L94.66924069514545 334.44339480993204 L95.62986211265076 334.26893636987535 L96.59048353015604 334.081346730362 L97.55110494766132 333.8806228884137 L98.5117263651666 333.666834406749 L99.47234778267187 333.4401193777365 L100.43296920017718 333.20067913894803 L101.39359061768243 332.948771684899 L102.35421203518771 332.6847037486366 L103.314833452693 332.40882156228844 L104.27545487019827 332.1215003466028 L105.23607628770355 331.82313262465726 L106.19669770520883 331.5141155027523 L107.15731912271414 331.19483711026277 L108.11794054021942 330.86566243792595 L109.0785619577247 330.5269188586305 L110.03918337522998 330.1788816541203 L110.99980479273526 329.82175990310174 L111.96042621024054 329.45568310913296 L112.92104762774579 329.08068895872344 L113.8816690452511 328.69671259994004 L114.84229046275638 328.3035778185556 L115.80291188026166 327.9009904619108 L116.76353329776694 327.488534420200

If we specify weights, `Stat.densityWeighted` mapped to `y` by default:

In [11]:
import org.jetbrains.kotlinx.statistics.dataframe.stat.mean

df.plot {
    densityPlot(depth, coeff, n = 700, adjust = 0.8, bandWidth = BandWidth.value(17.0))
    // we can add other layers as well
    // let's add a horizontal markline with constant y intercept:
    vLine {
         // count sample mean
        val mean = depth.mean()
        xIntercept.constant(mean)
        tooltips() { line("Depth mean: ${String.format("%.2f", mean)}m") }
        color = Color.RED; width = 2.0
    }
    x.axis.name = "depth, m"
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 0.0040
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M23.455612836968818 342.6466846828322 L23.455612836968818 342.6466846828322 L24.126731945322724 342.6442226067816 L24.79785105367663 342.64767529160184 L25.468970162030523 342.65660355768046 L26.14008927038443 342.6704182153459 L26.81120837873832 342.68838651075845 L27.482327487092228 342.70964198979004 L28.15344659544612 342.7331975342262 L28.824565703800026 342.75796124557775 L29.495684812153932 342.7827547889998 L30.16680392050784 342.8063337642733 L30.83792302886173 342.8274096423211 L31.509042137215637 342.84467279302913 L32.18016124556953 342.8568161310923 L32.851280353923435 342.86255891847026 L33.52239946227733 342.8606702818195 L34.193518570631234 342.8499920280108 L34.864637678985126 342.8294603679549 L35.53575678733903 342.79812618645883 L36.206875895692924 342.75517352253075 L36.877995004046845 342.6999359501171 L37.54911411240072 342.631910574213 L38.22023322075464 342.5507693828793 L38.891352329108535 342.4563677236752 L39.56247143746244 342.34874970534946 L40.233590545816334 342.2281503642121 L40.90470965417024 342.09499448089963 L41.57582876252413 341.94989198803086 L42.24694787087804 341.7936299723927 L42.91806697923193 341.62716134562436 L43.58918608758584 341.45159033269044 L44.26030519593974 341.26815500462385 L44.931424304293635 341.0782071572873 L45.60254341264753 340.88318990710127 L46.273662521001434 340.68461343372945 L46.94478162935534 340.48402934498864 L47.61590073770923 340.2830041680484 L48.28701984606314 340.08309248180535 L48.95813895441703 339.885810198147 L49.62925806277094 339.692608476176 L50.30037717112483 339.50484871636496 L50.97149627947875 339.32377903529635 L51.64261538783263 339.15051257120444 L52.31373449618655 338.98600792138143 L52.984853604540454 338.8310519697771 L53.655972712894346 338.68624533104105 L54.32709182124824 338.55199061859935 L54.998210929602145 338.42848373995537 L55.66933003795605 338.3157084308699 L56.34044914630994 338.21343425770823 L57.011568254663835 338.1212183382069 L57.68268736301774 338.0384110476483 L58.35380647137165 337.9641659812781 L59.02492557972554 337.8974544258509 L59.696044688079446 337.83708454521 L60.36716379643334 337.781725400235 L61.038282904787245 337.72993579836884 L61.70940201314114 337.6801978016805 L62.38052112149504 337.63095451838944 L63.051640229848935 337.5806515685116 L63.722759338202856 337.5277813613868 L64.39387844655676 337.4709290665159 L65.06499755491066 337.4088189173065 L65.73611666326454 337.3403592795188 L66.40723577161845 337.26468476208964 L67.07835487997235 337.18119356589693 L67.74947398832626 337.089578271208 L68.42059309668014 336.9898483679155 L69.09171220503404 336.8823430393452 L69.76283131338795 336.7677330189671 L70.43395042174186 336.64701074120967 L71.10506953009573 336.5214684871553 L71.77618863844964 336.3926647610867 L72.44730774680355 336.2623796971377 L73.11842685515745 336.1325608552798 L73.78954596351136 336.0052612891878 L74.46066507186524 335.8825722220126 L75.13178418021914 335.76655301904714 L75.80290328857308 335.65916137266044 L76.47402239692696 335.5621866953 L77.14514150528083 335.47718963965264 L77.81626061363477 335.4054504293761 L78.48737972198867 335.3479282971498 L79.15849883034255 335.305233806772 L79.82961793869643 335.27761520911156 L80.50073704705034 335.2649592817127 L81.17185615540424 335.2668063679409 L81.84297526375815 335.2823786059025 L82.51409437211205 335.31061966242913 L83.18521348046593 335.3502437032645 L83.85633258881987 335.3997908722751 L84.52745169717377 335.45768624777565 L85.19857080552765 335.5222991115148 L85.86968991388153 335.5919994137113 L86.54080902223546 335.66520

### `densityPlot` plot

`densityPlot(statDensityArgs)` and `DataFrame.densityPlot(statDensityArgs)` is a family of functions for fast plotting a density plot.

In [12]:
densityPlot(depthList, kernel = Kernel.COSINE)

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 0.0040
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M23.455612836968818 340.6495084537616 L23.455612836968818 340.6495084537616 L24.3736407366545 340.6783435377016 L25.291668636340155 340.7638561446464 L26.209696536025824 340.9031025116703 L27.127724435711492 341.09128909654083 L28.04575233539716 341.3219375949302 L28.963780235082844 341.5871079553923 L29.881808134768498 341.8776717148383 L30.799836034454167 342.1836262449637 L31.717863934139835 342.4944390917256 L32.635891833825504 342.79941055401764 L33.55391973351117 343.0880420198085 L34.47194763319684 343.35039737980924 L35.38997553288251 343.5774450770398 L36.30800343256818 343.75563972308385 L37.22603133225385 343.8357982298162 L38.144059231939515 343.80626903027394 L39.06208713162517 343.6683141728932 L39.98011503131084 343.4603292673333 L40.89814293099652 343.21325230479033 L41.81617083068219 342.93558888494283 L42.73419873036786 342.6368975431971 L43.65222663005351 342.3274606990639 L44.57025452973918 341.99794513684805 L45.48828242942486 341.6228243741 L46.40631032911053 341.19946165024464 L47.32433822879619 340.70185553551494 L48.242366128481855 340.1447772098609 L49.160394028167524 339.54740403882397 L50.07842192785319 338.901533861863 L50.996449827538875 338.20049724029855 L51.91447772722454 337.4684272486066 L52.8325056269102 336.7305253228978 L53.750533526595866 336.01219366302684 L54.668561426281535 335.3381607644081 L55.58658932596719 334.7316301420384 L56.50461722565287 334.2134815518186 L57.42264512533854 333.8015522070484 L58.34067302502421 333.51002273414633 L59.25870092470988 333.3489290060058 L60.176728824395546 333.32381665807645 L61.0947567240812 333.4355501804195 L62.01278462376688 333.680283157724 L62.93081252345255 334.0379853162411 L63.84884042313822 334.4541531776244 L64.76686832282388 334.9105850199741 L65.68489622250954 335.3779928452776 L66.60292412219522 335.7990486865621 L67.5209520218809 336.16784741298244 L68.43897992156656 336.51394868659617 L69.35700782125224 336.82940568717146 L70.2750357209379 337.1033588390722 L71.19306362062355 337.32637733249436 L72.11109152030923 337.4907837781483 L73.02911941999488 337.5909185006159 L73.94714731968057 337.62333437210964 L74.86517521936622 337.5869232943822 L75.7832031190519 337.51270361408183 L76.70123101873759 337.43112779031964 L77.61925891842324 337.36830304142495 L78.53728681810892 337.36046622172216 L79.45531471779455 337.40065413646164 L80.37334261748023 337.41442639768763 L81.29137051716589 337.4049644854665 L82.20939841685157 337.39185533849064 L83.12742631653722 337.37555023783113 L84.04545421622291 337.3566104849444 L84.96348211590859 337.3356880789258 L85.88151001559424 337.3135032715061 L86.79953791527993 337.29081977245784 L87.71756581496558 337.2684184589628 L88.63559371465124 337.24707049399353 L89.55362161433692 337.227510779105 L90.47164951402257 337.21041265552236 L91.38967741370826 337.17142182150906 L92.30770531339391 337.0792954388678 L93.2257332130796 336.93706277788874 L94.14376111276525 336.7689396221081 L95.06178901245093 336.618108048454 L95.97981691213661 336.48783341287316 L96.89784481182227 336.3631682259727 L97.81587271150792 336.2702301144501 L98.73390061119358 336.210568249421 L99.65192851087926 336.1403343275328 L100.56995641056491 336.0036103519161 L101.4879843102506 335.7945364261335 L102.40601220993628 335.44672207593493 L103.32404010962193 334.93199211819353 L104.24206800930762 334.2680660801286 L105.16009590899327 333.47779954907526 L106.07812380867892 332.56777414730846 L106.99615170836461 331.5329619941503 L107.91417960805026 330.40829486422615 L108.83220750773594 329.23248931079206 L109.7502354074216 328.046022

In [13]:
df.densityPlot("depth")

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M23.455612836968818 341.9998511643638 L23.455612836968818 341.9998511643638 L24.3736407366545 341.93522936228413 L25.291668636340155 341.86908123936433 L26.209696536025824 341.800957823164 L27.127724435711492 341.7303776823555 L28.04575233539716 341.6568355421832 L28.963780235082844 341.57981200158355 L29.881808134768498 341.4987841768706 L30.799836034454167 341.4132370650941 L31.717863934139835 341.3226753926651 L32.635891833825504 341.2266356925614 L33.55391973351117 341.1246983371758 L34.47194763319684 341.0164992443051 L35.38997553288251 340.9017409713754 L36.30800343256818 340.78020291802335 L37.22603133225385 340.6517503696769 L38.144059231939515 340.51634213463973 L39.06208713162517 340.3740365540187 L39.98011503131084 340.22499569705514 L40.89814293099652 340.06948759325525 L41.81617083068219 339.9078863962053 L42.73419873036786 339.74067042099506 L43.65222663005351 339.5684180465289 L44.57025452973918 339.3918015243556 L45.48828242942486 339.2115787856287 L46.40631032911053 339.0285833860378 L47.32433822879619 338.843712773676 L48.242366128481855 338.6579151055575 L49.160394028167524 338.47217487370443 L50.07842192785319 338.28749763037086 L50.996449827538875 338.1048941232388 L51.91447772722454 337.9253641646867 L52.8325056269102 337.74988056411905 L53.750533526595866 337.5793734487275 L54.668561426281535 337.41471528606394 L55.58658932596719 337.2567069018279 L56.50461722565287 337.1060647589491 L57.42264512533854 336.96340973024076 L58.34067302502421 336.82925755768133 L59.25870092470988 336.70401114798483 L60.176728824395546 336.58795480790303 L61.0947567240812 336.4812504751012 L62.01278462376688 336.3839359529311 L62.93081252345255 336.2959251114343 L63.84884042313822 336.2170099738044 L64.76686832282388 336.14686456857316 L65.68489622250954 336.08505039402985 L66.60292412219522 336.03102331370576 L67.5209520218809 335.98414168079375 L68.43897992156656 335.94367547549564 L69.35700782125224 335.9088162326108 L70.2750357209379 335.87868753703145 L71.19306362062355 335.852355871783 L72.11109152030923 335.8288416161744 L73.02911941999488 335.80713000965005 L73.94714731968057 335.78618191902405 L74.86517521936622 335.76494427176505 L75.7832031190519 335.742360044663 L76.70123101873759 335.7173777242734 L77.61925891842324 335.6889601817802 L78.53728681810892 335.6560929291831 L79.45531471779455 335.61779174497724 L80.37334261748023 335.57310967489184 L81.29137051716589 335.52114342613436 L82.20939841685157 335.4610391815264 L83.12742631653722 335.3919978627407 L84.04545421622291 335.31327986964214 L84.96348211590859 335.22420931583736 L85.88151001559424 335.1241777695296 L86.79953791527993 335.0126474944689 L87.71756581496558 334.88915416917 L88.63559371465124 334.75330904479245 L89.55362161433692 334.6048004843902 L90.47164951402257 334.44339480993204 L91.38967741370826 334.26893636987535 L92.30770531339391 334.081346730362 L93.2257332130796 333.8806228884137 L94.14376111276525 333.666834406749 L95.06178901245093 333.4401193777365 L95.97981691213661 333.20067913894803 L96.89784481182227 332.948771684899 L97.81587271150792 332.6847037486366 L98.73390061119358 332.40882156228844 L99.65192851087926 332.1215003466028 L100.56995641056491 331.82313262465726 L101.4879843102506 331.5141155027523 L102.40601220993628 331.19483711026277 L103.32404010962193 330.86566243792595 L104.24206800930762 330.5269188586305 L105.16009590899327 330.1788816541203 L106.07812380867892 329.82175990310174 L106.99615170836461 329.45568310913296 L107.91417960805026 329.08068895872344 L108.83220750773594 328.69671259994004 L109.7502354074216 328.3035778185556 L110.6682633071

In case you want to provide input and weights using column selection DSL, it's a bit different from the usual one - you should assign `x` input and (optionally) `weight` throw invocation eponymous functions:

In [14]:
df.densityPlot(adjust = 0.5) {
    x(depth)
    weight(coeff)
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 0.0040
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M23.455612836968818 342.4687391006937 L23.455612836968818 342.4687391006937 L24.3736407366545 342.47676243192353 L25.291668636340155 342.5044171670303 L26.209696536025824 342.54993156589603 L27.127724435711492 342.61062055354523 L28.04575233539716 342.6829953174837 L28.963780235082844 342.7629104222211 L29.881808134768498 342.84573545456175 L30.799836034454167 342.9265379149888 L31.717863934139835 343.0002654911799 L32.635891833825504 343.0619186141248 L33.55391973351117 343.1067077183213 L34.47194763319684 343.13019320927646 L35.38997553288251 343.128409102737 L36.30800343256818 343.0979730961751 L37.22603133225385 343.0361861565465 L38.144059231939515 342.9411235491497 L39.06208713162517 342.81171688690193 L39.98011503131084 342.64782380392904 L40.89814293099652 342.4502789722583 L41.81617083068219 342.22091813732743 L42.73419873036786 341.9625662832533 L43.65222663005351 341.67898233714965 L44.57025452973918 341.374756017991 L45.48828242942486 341.05515717516886 L46.40631032911053 340.72594353549886 L47.32433822879619 340.3931382285999 L48.242366128481855 340.06279275451476 L49.160394028167524 339.74075328264144 L50.07842192785319 339.43244773622155 L50.996449827538875 339.1427079023535 L51.91447772722454 338.8756352362817 L52.8325056269102 338.6345120308066 L53.750533526595866 338.4217524934404 L54.668561426281535 338.2388824480739 L55.58658932596719 338.08653314479375 L56.50461722565287 337.96443489490673 L57.42264512533854 337.87140019144357 L58.34067302502421 337.80529313530855 L59.25870092470988 337.76299116505896 L60.176728824395546 337.74035455002456 L61.0947567240812 337.7322268681814 L62.01278462376688 337.73249387071104 L62.93081252345255 337.73422731386955 L63.84884042313822 337.7299338536084 L64.76686832282388 337.7119172286647 L65.68489622250954 337.6727459555641 L66.60292412219522 337.60580071779196 L67.5209520218809 337.5058582092936 L68.43897992156656 337.36965422805093 L69.35700782125224 337.19636089453655 L70.2750357209379 336.9879129073342 L71.19306362062355 336.74912664928297 L72.11109152030923 336.48757341080864 L73.02911941999488 336.2131924360777 L73.94714731968057 335.9376582425595 L74.86517521936622 335.67354623346745 L75.7832031190519 335.43336717394544 L76.70123101873759 335.2285609531119 L77.61925891842324 335.0685502039825 L78.53728681810892 334.95995293447515 L79.45531471779455 334.9060399147799 L80.37334261748023 334.90649831854313 L81.29137051716589 334.9575306522624 L82.20939841685157 335.0522811238591 L83.12742631653722 335.1815447830072 L84.04545421622291 335.3346825989515 L84.96348211590859 335.50064219710225 L85.88151001559424 335.6689722532908 L86.79953791527993 335.8307200591494 L87.71756581496558 335.97911634337305 L88.63559371465124 336.1099772097838 L89.55362161433692 336.22178676574356 L90.47164951402257 336.3154614276495 L91.38967741370826 336.3938333783912 L92.30770531339391 336.46092182134646 L93.2257332130796 336.5210829412611 L94.14376111276525 336.5781405132048 L95.06178901245093 336.63459807533644 L95.97981691213661 336.69102121931263 L96.89784481182227 336.7456569266888 L97.81587271150792 336.79432904696455 L98.73390061119358 336.83061852913295 L99.65192851087926 336.84630742512655 L100.56995641056491 336.832040046677 L101.4879843102506 336.7781352320119 L102.40601220993628 336.67547174113014 L103.32404010962193 336.51636465137534 L104.24206800930762 336.2953537556615 L105.16009590899327 336.0098342954495 L106.07812380867892 335.6604745225616 L106.99615170836461 335.25138216078875 L107.91417960805026 334.7900015127678 L108.83220750773594 334.28674355720733 L109.7502354074216 3

`densityPlot` plot can be configured with `.configure {}` extension - it opens context that combines area, `StatDensity` and plot context; that means you can configure bars settings, mappings using `StatDensity` dataset and any plot adjustments:

In [15]:
df.densityPlot() {
    x(depth)
}.configure {
    // Area + StatDensity + PlotContext
    // can't add new layer
    // can add area mapping, including for `Stat.*` columns
    fillColor(Stat.scaled) // doesn't work properly for now
    alpha = 0.6
    // can configure general plot adjustments
    layout {
        title = "Configured `densityPlot` plot"
        size = 600 to 350
    }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.0000
 
 
 
 
 
 
 0.0005
 
 
 
 
 
 
 0.0010
 
 
 
 
 
 
 0.0015
 
 
 
 
 
 
 0.0020
 
 
 
 
 
 
 0.0025
 
 
 
 
 
 
 0.0030
 
 
 
 
 
 
 0.0035
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M20.187613662841933 268.4301157394716 L20.187613662841933 268.4301157394716 L20.9777355283152 268.37939513900204 L21.767857393788454 268.3274765541522 L22.55797925926172 268.27400759376246 L23.34810112473499 268.2186103902209 L24.138222990208256 268.16088836159724 L24.928344855681523 268.1004338384522 L25.71846672115479 268.03683641789263 L26.508588586628058 267.96969188248664 L27.29871045210131 267.89861150005686 L28.088832317574578 267.8232315028825 L28.878954183047846 267.74322253208567 L29.669076048521113 267.658298825472 L30.459197913994366 267.5682269252074 L31.249319779467648 267.47283368565786 L32.039441644940915 267.37201337154875 L32.82956351041418 267.2657336521882 L33.619685375887435 267.1540403185612 L34.4098072413607 267.037060576177 L35.19992910683397 266.9150047970317 L35.99005097230724 266.78816664818436 L36.780172837780505 266.6569215513624 L37.57029470325376 266.52172346675235 L38.360416568727025 266.3831000336512 L39.15053843420029 266.241646139883 L39.94066029967356 266.098016029739 L40.73078216514681 265.95291409561776 L41.52090403062008 265.8070845305248 L42.31102589609335 265.6613000462215 L43.101147761566615 265.5163498843027 L43.89126962703988 265.37302736417 L44.681391492513164 265.2321172222832 L45.4715133579864 265.0943830009074 L46.261635223459685 264.9605547417338 L47.05175708893295 264.83131723034086 L47.841878954406205 264.7072990217835 L48.63200081987947 264.5890624561519 L49.42212268535274 264.4770948464099 L50.21224455082601 264.3718009900406 L51.002366416299274 264.2734971219648 L51.79248828177254 264.1824063899239 L52.582610147245795 264.098655896155 L53.37273201271906 264.0222753118936 L54.16285387819233 263.9531970351374 L54.9529757436656 263.8912578282767 L55.74309760913885 263.83620184161265 L56.53321947461212 263.7876849022909 L57.323341340085385 263.7452799264551 L58.11346320555865 263.7084832959718 L58.90358507103192 263.67672203018554 L59.69370693650519 263.64936157792124 L60.48382880197844 263.6257140552282 L61.27395066745172 263.6050467598297 L62.06407253292499 263.58659080339265 L62.85419439839824 263.56954971687645 L63.64431626387151 263.55310790155954 L64.43443812934478 263.5364388179551 L65.22455999481804 263.5187128257529 L66.01468186029132 263.49910460916806 L66.80480372576457 263.4768001426763 L67.59492559123785 263.4510031711612 L68.3850474567111 263.4209411951856 L69.17516932218436 263.3858709657581 L69.96529118765761 263.34508350307055 L70.7554130531309 263.297908659919 L71.54553491860415 263.24371925273255 L72.33565678407743 263.1819347814052 L73.12577864955068 263.11202475370953 L73.91590051502396 263.0335116214331 L74.70602238049722 262.94597332414713 L75.49614424597047 262.84904542347647 L76.28626611144375 262.7424227967848 L77.07638797691703 262.62586084530625 L77.86650984239029 262.49917615895833 L78.65663170786354 262.3622465693789 L79.44675357333682 262.2150105151097 L80.23687543881007 262.05746563916193 L81.02699730428336 261.8896665401809 L81.81711916975661 261.7117216046188 L82.60724103522989 261.523788859058 L83.39736290070314 261.326070799194 L84.1874847661764 261.118808174802 L84.97760663164965 260.9022727378427 L85.76772849712293 260.67675899297313 L86.55785036259618 260.442575025167 L87.34797222806947 260.2000325166951 L88.13809409354272 259.9494361039853 L88.928215959016 259.69107226232563 L89.71833782448925 259.42519794136695 L90.5084596899625 259.15202920526883 L91.29858155543579 258.87173015650427 L92.08870342090904 258.5844024403078 L92.8788252863823 258.29007563620735 L93.66894715185558 257.9886988429762 L94.45906901732883 257.6801337529361 L95.24919088280211 257.36414949045

## Grouped `statDensity`

`statCount` can be applied for grouped data - statistics will be calculated on each group independently but with equal categories. This application returns a new `GroupBy` dataset with the same keys as the old one but with `StatCount` groups instead of old ones.

In [16]:
// create two samples from normal distribution with different mean/std
val rangesA = NormalDistribution(500.0, 100.0).sample(5000).toList()
val rangesB = NormalDistribution(400.0, 80.0).sample(5000).toList()

In [17]:
// gather them into `DataFrame` with "A" and "B" keys in "category" column
val rangesDF = dataFrameOf(
    "range" to rangesA + rangesB,
    "category" to List(5000) { "A" } + List(5000) { "B" }
)
rangesDF.head(5)

<iframe onload="o_resize_iframe_out_3()" style="width:100%;" class="result_container" id="iframe_out_3" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-385875966"></table>

<p class="dataframe_description">DataFrame: rowsCount = 5, columnsCount = 2</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i

It has the following signature:

<table>
  <thead>
    <tr>
      <th>range</th>
      <th>category</th>
    </tr>
  </thead>
</table>

In [18]:
// group it by "category"
val groupedRangesDF = rangesDF.groupBy { category }
groupedRangesDF

<iframe onload="o_resize_iframe_out_4()" style="width:100%;" class="result_container" id="iframe_out_4" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-385875965"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.length; i++) {
 if (df.c

Now we have a `GroupBy` with a signature

<table>
  <thead>
    <tr>
      <th>key: [category]</th>
      <th>group: DataFrame[range|category]</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>A</td>
      <td>A-Group</td>
    </tr>
    <tr>
      <td>B</td>
      <td>B-Group</td>
    </tr>
  </tbody>
</table>

In [19]:
groupedRangesDF.statDensity { x(range) }

<iframe onload="o_resize_iframe_out_5()" style="width:100%;" class="result_container" id="iframe_out_5" frameBorder="0" srcdoc=" <html>
 <head>
 <style type="text/css">
 :root {
 --background: #fff;
 --background-odd: #f5f5f5;
 --background-hover: #d9edfd;
 --header-text-color: #474747;
 --text-color: #848484;
 --text-color-dark: #000;
 --text-color-medium: #737373;
 --text-color-pale: #b3b3b3;
 --inner-border-color: #aaa;
 --bold-border-color: #000;
 --link-color: #296eaa;
 --link-color-pale: #296eaa;
 --link-hover: #1a466c;
}

:root[theme="dark"], :root [data-jp-theme-light="false"], .dataframe_dark{
 --background: #303030;
 --background-odd: #3c3c3c;
 --background-hover: #464646;
 --header-text-color: #dddddd;
 --text-color: #b3b3b3;
 --text-color-dark: #dddddd;
 --text-color-medium: #b2b2b2;
 --text-color-pale: #737373;
 --inner-border-color: #707070;
 --bold-border-color: #777777;
 --link-color: #008dc0;
 --link-color-pale: #97e1fb;
 --link-hover: #00688e;
}

p.dataframe_description {
 color: var(--text-color-dark);
}

table.dataframe {
 font-family: "Helvetica Neue", Helvetica, Arial, sans-serif;
 font-size: 12px;
 background-color: var(--background);
 color: var(--text-color-dark);
 border: none;
 border-collapse: collapse;
}

table.dataframe th, td {
 padding: 6px;
 border: 1px solid transparent;
 text-align: left;
}

table.dataframe th {
 background-color: var(--background);
 color: var(--header-text-color);
}

table.dataframe td {
 vertical-align: top;
}

table.dataframe th.bottomBorder {
 border-bottom-color: var(--bold-border-color);
}

table.dataframe tbody > tr:nth-child(odd) {
 background: var(--background-odd);
}

table.dataframe tbody > tr:nth-child(even) {
 background: var(--background);
}

table.dataframe tbody > tr:hover {
 background: var(--background-hover);
}

table.dataframe a {
 cursor: pointer;
 color: var(--link-color);
 text-decoration: none;
}

table.dataframe tr:hover > td a {
 color: var(--link-color-pale);
}

table.dataframe a:hover {
 color: var(--link-hover);
 text-decoration: underline;
}

table.dataframe img {
 max-width: fit-content;
}

table.dataframe th.complex {
 background-color: var(--background);
 border: 1px solid var(--background);
}

table.dataframe .leftBorder {
 border-left-color: var(--inner-border-color);
}

table.dataframe .rightBorder {
 border-right-color: var(--inner-border-color);
}

table.dataframe .rightAlign {
 text-align: right;
}

table.dataframe .expanderSvg {
 width: 8px;
 height: 8px;
 margin-right: 3px;
}

table.dataframe .expander {
 display: flex;
 align-items: center;
}

/* formatting */

table.dataframe .null {
 color: var(--text-color-pale);
}

table.dataframe .structural {
 color: var(--text-color-medium);
 font-weight: bold;
}

table.dataframe .dataFrameCaption {
 font-weight: bold;
}

table.dataframe .numbers {
 color: var(--text-color-dark);
}

table.dataframe td:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}

table.dataframe tr:hover .formatted .structural, .null {
 color: var(--text-color-dark);
}




:root {
 --scroll-bg: #f5f5f5;
 --scroll-fg: #b3b3b3;
}
:root[theme="dark"], :root [data-jp-theme-light="false"]{
 --scroll-bg: #3c3c3c;
 --scroll-fg: #97e1fb;
}
body {
 scrollbar-color: var(--scroll-fg) var(--scroll-bg);
}
body::-webkit-scrollbar {
 width: 10px; /* Mostly for vertical scrollbars */
 height: 10px; /* Mostly for horizontal scrollbars */
}
body::-webkit-scrollbar-thumb {
 background-color: var(--scroll-fg);
}
body::-webkit-scrollbar-track {
 background-color: var(--scroll-bg);
}
 </style>
 </head>
 <body>
 
<table class="dataframe" id="df_-385875962"></table>

<p class="dataframe_description">GroupBy</p>

 </body>
 <script>
 (function () {
 window.DataFrame = window.DataFrame || new (function () {
 this.addTable = function (df) {
 let cols = df.cols;
 for (let i = 0; i < cols.length; i++) {
 for (let c of cols[i].children) {
 cols[c].parent = i;
 }
 }
 df.nrow = 0
 for (let i = 0; i < df.cols.length; i++) {
 if (df.c

After `statDensity` applying it's still a `GroupBy` but with different signature of `group` - all groups have the same signature as usual `DataFrame` after `statDensity` applying (i.e. `StatDensityFrame`):

<table>
  <thead>
    <tr>
      <th>key: [drv]</th>
      <th>group: StaDensityFrame</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <td>"A"</td>
      <td>"A"-Group</td>
    </tr>
    <tr>
      <td>"B"</td>
      <td>"B"-Group</td>
    </tr>
  </tbody>
</table>

As you can see, we did indeed do a `statDensity` transformation within groups, the grouping keys did not change.

The plotting process doesn't change much - we do everything the same. 

In [20]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
        }
    }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M23.818367630399194 328.235116002668 L23.818367630399194 328.235116002668 L25.682819108316934 328.23874504507626 L27.54727058623469 328.25035544141576 L29.41172206415243 328.26846350818533 L31.27617354207017 328.29084583098097 L33.14062501998792 328.3147131426411 L35.00507649790566 328.33691722974925 L36.86952797582342 328.3541593328054 L38.733979453741156 328.36317863943543 L40.598430931658896 328.3609138767638 L42.462882409576636 328.3446441748435 L44.327333887494376 328.3121222560647 L46.191785365412144 328.2617107842034 L48.056236843329884 328.1925218473825 L49.920688321247624 328.1045438246371 L51.785139799165364 327.9987252879256 L53.649591277083104 327.87697841721445 L55.51404275500087 327.74206908187927 L57.3784942329186 327.59737809360786 L59.24294571083635 327.44654474760944 L61.10739718875409 327.2930327558187 L62.97184866667183 327.139681732929 L64.83630014458959 326.98831747358867 L66.70075162250733 326.839487919863 L68.56520310042508 326.6923702857802 L70.4296545783428 326.544863848814 L72.29410605626057 326.3938502750011 L74.15855753417831 326.23557649240655 L76.02300901209605 326.0660989483906 L77.8874604900138 325.8817238635331 L79.75191196793153 325.6793839983403 L81.6163634458493 325.4569050846657 L83.48081492376703 325.2131312578403 L85.34526640168478 324.9478967143759 L87.20971787960254 324.6618499323597 L89.07416935752026 324.35615702616485 L90.93862083543802 324.03213105750973 L92.80307231335574 323.6908512904742 L94.66752379127352 323.3328454221881 L96.53197526919122 322.9579031102904 L98.396426747109 322.5650667467019 L100.26087822502673 322.1528057550692 L102.12532970294448 321.7193300639743 L103.98978118086221 321.2629490846588 L105.85423265877996 320.7823502345596 L107.71868413669772 320.2766704583312 L109.58313561461544 319.74527337376963 L111.4475870925332 319.1872204785696 L113.31203857045095 318.60052131954745 L115.1764900483687 317.98133852119463 L117.04094152628643 317.32337977069835 L118.90539300420419 316.6177071435145 L120.76984448212191 315.8531263180827 L122.63429596003967 315.01719558999264 L124.49874743795742 314.0977463016193 L126.36319891587517 313.0846712881778 L128.22765039379289 311.97165300036335 L130.0921018717106 310.7574910597814 L131.9565533496284 309.44675207196383 L133.82100482754618 308.049583485266 L135.6854563054639 306.58067530475216 L137.54990778338163 305.0574837110041 L139.41435926129935 303.49792403577476 L141.27881073921714 301.9177891003366 L143.14326221713486 300.32816164825743 L145.0077136950526 298.7330853390511 L146.8721651729703 297.12775480696433 L148.7366166508881 295.4974867699421 L150.60106812880588 293.81772907717027 L152.4655196067236 292.05532715095063 L154.32997108464133 290.1711693206381 L155.26219682360022 289.1705347835093 L156.19442256255905 288.12415865220714 L157.126648301518 287.02741691661737 L158.05887404047684 285.8762194211007 L158.99109977943573 284.6671812067139 L159.92332551839456 283.39778238781474 L160.8555512573534 282.06650926654487 L161.7877769963123 280.67296959077487 L162.72000273527118 279.2179754550519 L163.65222847423007 277.7035883268351 L164.58445421318896 276.1331220222057 L165.5166799521478 274.5111011008658 L166.4489056911067 272.84317402110224 L167.38113143006558 271.13598239492376 L168.3133571690244 269.39698970308393 L169.2455829079833 267.6342747561938 L170.17780864694214 265.8562969116623 L171.11003438590103 264.0716414780062 L172.04226012485992 262.2887547770569 L172.97448586381876 260.5156789330441 L173.9067116027777 258.75979658461677 L174.83893734173654 257.02759536931745 L175.77116308069537 255.324461235284 L176.70338881965426 253.6545084426382 L177.6356145586131 252.02045259811138 L178.56

As you can see, there are two lines because we have three groups of data. To distinguish them, we need to add mapping to the color from the key. This is easy - key is available in the context

In [21]:
groupedRangesDF.plot {
    statDensity(range) {
        line {
            x(Stat.x)
            y(Stat.density)
            color(key.category)
        }
    }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M19.865713083991892 328.235116002668 L19.865713083991892 328.235116002668 L21.420759117963854 328.23874504507626 L22.97580515193583 328.25035544141576 L24.530851185907792 328.26846350818533 L26.085897219879755 328.29084583098097 L27.64094325385173 328.3147131426411 L29.195989287823693 328.33691722974925 L30.75103532179567 328.3541593328054 L32.30608135576763 328.36317863943543 L33.86112738973959 328.3609138767638 L35.416173423711555 328.3446441748435 L36.97121945768353 328.3121222560647 L38.52626549165551 328.2617107842034 L40.08131152562747 328.1925218473825 L41.63635755959943 328.1045438246371 L43.19140359357141 327.9987252879256 L44.74644962754337 327.87697841721445 L46.30149566151535 327.74206908187927 L47.856541695487294 327.59737809360786 L49.411587729459285 327.44654474760944 L50.96663376343125 327.2930327558187 L52.52167979740321 327.139681732929 L54.07672583137517 326.98831747358867 L55.63177186534713 326.839487919863 L57.186817899319124 326.6923702857802 L58.74186393329107 326.544863848814 L60.29690996726305 326.3938502750011 L61.85195600123501 326.23557649240655 L63.407002035206986 326.0660989483906 L64.96204806917895 325.8817238635331 L66.51709410315091 325.6793839983403 L68.07214013712289 325.4569050846657 L69.62718617109485 325.2131312578403 L71.18223220506682 324.9478967143759 L72.73727823903879 324.6618499323597 L74.29232427301075 324.35615702616485 L75.84737030698273 324.03213105750973 L77.40241634095469 323.6908512904742 L78.95746237492666 323.3328454221881 L80.51250840889861 322.9579031102904 L82.0675544428706 322.5650667467019 L83.62260047684256 322.1528057550692 L85.17764651081453 321.7193300639743 L86.73269254478649 321.2629490846588 L88.28773857875845 320.7823502345596 L89.84278461273043 320.2766704583312 L91.39783064670239 319.74527337376963 L92.95287668067438 319.1872204785696 L94.50792271464634 318.60052131954745 L96.0629687486183 317.98133852119463 L97.61801478259027 317.32337977069835 L99.17306081656223 316.6177071435145 L100.72810685053419 315.8531263180827 L102.28315288450615 315.01719558999264 L103.83819891847814 314.0977463016193 L105.39324495245013 313.0846712881778 L106.94829098642207 311.97165300036335 L108.50333702039403 310.7574910597814 L110.05838305436599 309.44675207196383 L111.61342908833798 308.049583485266 L113.16847512230994 306.58067530475216 L114.7235211562819 305.0574837110041 L116.27856719025387 303.49792403577476 L117.83361322422583 301.9177891003366 L119.38865925819782 300.32816164825743 L120.94370529216978 298.7330853390511 L122.49875132614171 297.12775480696433 L124.0537973601137 295.4974867699421 L125.6088433940857 293.81772907717027 L127.16388942805766 292.05532715095063 L128.7189354620296 290.1711693206381 L129.4964584790156 289.1705347835093 L130.27398149600157 288.12415865220714 L131.0515045129876 287.02741691661737 L131.82902752997353 285.8762194211007 L132.6065505469595 284.6671812067139 L133.38407356394555 283.39778238781474 L134.16159658093147 282.06650926654487 L134.93911959791745 280.67296959077487 L135.7166426149035 279.2179754550519 L136.49416563188947 277.7035883268351 L137.27168864887545 276.1331220222057 L138.04921166586138 274.5111011008658 L138.82673468284742 272.84317402110224 L139.6042576998334 271.13598239492376 L140.38178071681932 269.39698970308393 L141.15930373380536 267.6342747561938 L141.93682675079134 265.8562969116623 L142.71434976777732 264.0716414780062 L143.4918727847633 262.2887547770569 L144.26939580174928 260.5156789330441 L145.04691881873526 258.75979658461677 L145.82444183572125 257.02759536931745 L146.60196485270723 255.324461235284 L147.3794878696932 253.6545084426382 L148.1570108866792 252.02045259811138 L148.934

The `densityPlot()` layer also works. Moreover, if we have exactly one grouping key, a mapping from it to `fillColor` and `borderLine.color` will be created by default.

In [22]:
groupedRangesDF.plot {
    densityPlot(range)
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M25.484270532552216 343.28418638518616 L25.484270532552216 343.28418638518616 L26.06615690826331 343.2426481412581 L26.648043283974417 343.19937694811335 L27.229929659685524 343.15407316074266 L27.811816035396618 343.106397210931 L28.39370241110774 343.0559738039986 L28.975588786818832 343.0023970602072 L29.55747516252994 342.94523642588155 L30.139361538241047 342.8840431691673 L30.72124791395214 342.8183572777563 L31.303134289663248 342.74771458944366 L31.885020665374356 342.6716540086075 L32.46690704108546 342.5897246893915 L33.04879341679657 342.5014930957708 L33.63067979250768 342.4065498759211 L34.21256616821877 342.30451650974896 L34.79445254392988 342.195051701076 L35.376338919640986 342.0778574877626 L35.95822529535208 341.9526850332177 L36.54011167106319 341.81934004185274 L37.121998046774294 341.6776877111372 L37.70388442248539 341.5276570973328 L38.285770798196495 341.369244735177 L38.8676571739076 341.2025173188907 L39.449543549618696 341.0276132283298 L40.0314299253298 340.8447426750275 L40.61331630104091 340.6541862526018 L41.19520267675203 340.45629170753074 L41.777089052463126 340.2514688008043 L42.35897542817423 340.04018220756217 L42.94086180388534 339.8229424973528 L43.522748179596434 339.60029534674703 L44.10463455530754 339.37280925142255 L44.68652093101865 339.1410621177205 L45.268407306729756 338.90562721449305 L45.85029368244085 338.6670590451848 L46.43218005815196 338.42587974876557 L47.014066433863064 338.18256664929726 L47.59595280957416 337.9375415430533 L48.177839185285265 337.6911622378292 L48.75972556099637 337.4437167435756 L49.341611936707466 337.1954203626155 L49.92349831241857 336.94641575078384 L50.50538468812968 336.6967758301113 L51.08727106384079 336.4465092434645 L51.66915743955188 336.1955678671404 L52.25104381526299 335.94385575377044 L52.832930190974096 335.6912387783691 L53.41481656668519 335.43755421541726 L53.99670294239631 335.1826194909463 L54.57858931810742 334.92623943236083 L55.160475693818526 334.6682114766373 L55.74236206952962 334.4083284858188 L56.32424844524073 334.1463790439088 L56.906134820951834 333.8821453540695 L57.48802119666293 333.615399099648 L58.069907572374035 333.3458958562358 L58.65179394808514 333.07336882471674 L59.233680323796236 332.79752277956266 L59.81556669950734 332.51802917901557 L60.39745307521845 332.2345233560981 L60.97933945092957 331.9466045996518 L61.561225826640666 331.65383974743366 L62.14311220235177 331.3557706597423 L62.72499857806288 331.05192563888374 L63.306884953773974 330.7418345284188 L63.88877132948508 330.4250468909809 L64.47065770519619 330.1011523501767 L65.0525440809073 329.7698019156166 L65.63443045661839 329.4307289127568 L66.2163168323295 329.0837680288514 L66.7982032080406 328.7288709749903 L67.3800895837517 328.3661173571132 L67.9619759594628 327.99571954389 L68.54386233517391 327.6180206069106 L69.125748710885 327.2334847723922 L69.70763508659611 326.8426802415309 L70.28952146230722 326.44625468233335 L70.87140783801833 326.0449041404755 L71.45329421372942 325.6393365311453 L72.03518058944053 325.23023123025666 L72.61706696515164 324.81819655767896 L73.19895334086273 324.4037271183305 L73.78083971657384 323.98716302683096 L74.36272609228494 323.5686529831888 L74.94461246799604 323.1481229938915 L75.52649884370715 322.7252522556925 L76.10838521941827 322.29945735629326 L76.69027159512937 321.869885520616 L77.27215797084047 321.43541717118467 L77.85404434655158 320.99467760599356 L78.43593072226268 320.54605715678093 L79.01781709797378 320.0877388022165 L79.59970347368488 319.61773189728734 L80.18158984939599 319.1339104593836 L80.7634762251071 318.6340543334646 L81.34536260081819 318.1158915457635 L81.9

We can customize it like we used to. From the differences — access to `key` columns:

In [23]:
groupedRangesDF.plot {
    densityPlot(column<Double>("range")) {
        // customize scale of default mapping
        fillColor(key.category) {
            scale = categorical("A" to Color.GREEN,  "B" to Color.ORANGE)
        }
        borderLine.color = Color.BLACK
        alpha = 0.5
    }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M25.484270532552216 343.28418638518616 L25.484270532552216 343.28418638518616 L26.06615690826331 343.2426481412581 L26.648043283974417 343.19937694811335 L27.229929659685524 343.15407316074266 L27.811816035396618 343.106397210931 L28.39370241110774 343.0559738039986 L28.975588786818832 343.0023970602072 L29.55747516252994 342.94523642588155 L30.139361538241047 342.8840431691673 L30.72124791395214 342.8183572777563 L31.303134289663248 342.74771458944366 L31.885020665374356 342.6716540086075 L32.46690704108546 342.5897246893915 L33.04879341679657 342.5014930957708 L33.63067979250768 342.4065498759211 L34.21256616821877 342.30451650974896 L34.79445254392988 342.195051701076 L35.376338919640986 342.0778574877626 L35.95822529535208 341.9526850332177 L36.54011167106319 341.81934004185274 L37.121998046774294 341.6776877111372 L37.70388442248539 341.5276570973328 L38.285770798196495 341.369244735177 L38.8676571739076 341.2025173188907 L39.449543549618696 341.0276132283298 L40.0314299253298 340.8447426750275 L40.61331630104091 340.6541862526018 L41.19520267675203 340.45629170753074 L41.777089052463126 340.2514688008043 L42.35897542817423 340.04018220756217 L42.94086180388534 339.8229424973528 L43.522748179596434 339.60029534674703 L44.10463455530754 339.37280925142255 L44.68652093101865 339.1410621177205 L45.268407306729756 338.90562721449305 L45.85029368244085 338.6670590451848 L46.43218005815196 338.42587974876557 L47.014066433863064 338.18256664929726 L47.59595280957416 337.9375415430533 L48.177839185285265 337.6911622378292 L48.75972556099637 337.4437167435756 L49.341611936707466 337.1954203626155 L49.92349831241857 336.94641575078384 L50.50538468812968 336.6967758301113 L51.08727106384079 336.4465092434645 L51.66915743955188 336.1955678671404 L52.25104381526299 335.94385575377044 L52.832930190974096 335.6912387783691 L53.41481656668519 335.43755421541726 L53.99670294239631 335.1826194909463 L54.57858931810742 334.92623943236083 L55.160475693818526 334.6682114766373 L55.74236206952962 334.4083284858188 L56.32424844524073 334.1463790439088 L56.906134820951834 333.8821453540695 L57.48802119666293 333.615399099648 L58.069907572374035 333.3458958562358 L58.65179394808514 333.07336882471674 L59.233680323796236 332.79752277956266 L59.81556669950734 332.51802917901557 L60.39745307521845 332.2345233560981 L60.97933945092957 331.9466045996518 L61.561225826640666 331.65383974743366 L62.14311220235177 331.3557706597423 L62.72499857806288 331.05192563888374 L63.306884953773974 330.7418345284188 L63.88877132948508 330.4250468909809 L64.47065770519619 330.1011523501767 L65.0525440809073 329.7698019156166 L65.63443045661839 329.4307289127568 L66.2163168323295 329.0837680288514 L66.7982032080406 328.7288709749903 L67.3800895837517 328.3661173571132 L67.9619759594628 327.99571954389 L68.54386233517391 327.6180206069106 L69.125748710885 327.2334847723922 L69.70763508659611 326.8426802415309 L70.28952146230722 326.44625468233335 L70.87140783801833 326.0449041404755 L71.45329421372942 325.6393365311453 L72.03518058944053 325.23023123025666 L72.61706696515164 324.81819655767896 L73.19895334086273 324.4037271183305 L73.78083971657384 323.98716302683096 L74.36272609228494 323.5686529831888 L74.94461246799604 323.1481229938915 L75.52649884370715 322.7252522556925 L76.10838521941827 322.29945735629326 L76.69027159512937 321.869885520616 L77.27215797084047 321.43541717118467 L77.85404434655158 320.99467760599356 L78.43593072226268 320.54605715678093 L79.01781709797378 320.0877388022165 L79.59970347368488 319.61773189728734 L80.18158984939599 319.1339104593836 L80.7634762251071 318.6340543334646 L81.34536260081819 318.1158915457635 L81.9

Also we can stack areas (for that we need `x` coordinates to match - use `trim = true`):

In [24]:
groupedRangesDF.plot {
    // use trim
    densityPlot(column<Double>("range"), trim = true) {
        // // adjust position of areas from diffrente groups
        position = Position.stack()
        alpha = 0.8
    }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 0.006
 
 
 
 
 
 
 0.007
 
 
 
 
 
 
 0.008
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M19.865713083991892 343.5587512971528 L19.865713083991892 343.5587512971528 L20.643236100977873 343.5324289822479 L21.420759117963854 343.5064269175432 L22.198282134949842 343.4807560666506 L22.97580515193583 343.4553420586572 L23.75332816892181 343.4300121480493 L24.530851185907792 343.4044855707045 L25.308374202893773 343.37836810950915 L26.085897219879755 343.3511513994294 L26.86342023686575 343.32221716697615 L27.64094325385173 343.29084625171765 L28.418466270837712 343.25623193914794 L29.195989287823693 343.217496882572 L29.973512304809688 343.1737127348906 L30.75103532179567 343.12392156311427 L31.52855833878165 343.06715817596125 L32.30608135576763 343.0024726378291 L33.083604372753626 342.9289524363934 L33.86112738973959 342.8457439728072 L34.63865040672559 342.7520732079281 L35.416173423711555 342.6472653863053 L36.19369644069755 342.5307637464746 L36.97121945768353 342.4021470052914 L37.74874247466951 342.2611451915152 L38.52626549165551 342.1076531369681 L39.303788508641475 341.9417406667334 L40.08131152562747 341.76365832671513 L40.85883454261345 341.57383741028826 L41.63635755959943 341.3728831464158 L42.41388057658543 341.1615602175337 L43.19140359357141 340.94077028397675 L43.96892661055739 340.71152186533766 L44.74644962754337 340.4748936971706 L45.52397264452935 340.2319934468562 L46.30149566151535 339.9839143242626 L47.07901867850133 339.73169255231915 L47.856541695487294 339.4762687810116 L48.63406471247329 339.2184562834917 L49.411587729459285 338.9589181620196 L50.18911074644525 338.69815486645757 L50.96663376343125 338.43650219376315 L51.744156780417214 338.1741387394903 L52.52167979740321 337.91110068006867 L53.299202814389204 337.64730094369304 L54.07672583137517 337.3825494155889 L54.854248848361166 337.11657090530446 L55.63177186534713 336.84901819471247 L56.40929488233313 336.5794785233586 L57.186817899319124 336.30747321723516 L57.96434091630509 336.0324516354462 L58.74186393329107 335.75378197292963 L59.51938695027707 335.4707424940889 L60.29690996726305 335.18251729474315 L61.07443298424903 334.8882005765241 L61.85195600123501 334.58681263413223 L62.62947901822099 334.27732936377885 L63.407002035206986 333.9587252550913 L64.18452505219297 333.63002775755047 L64.96204806917895 333.2903788902045 L65.73957108616491 332.93909827283153 L66.51709410315091 332.57574065107633 L67.2946171201369 332.20014065549253 L68.07214013712289 331.8124380707059 L68.84966315410887 331.41307828416626 L69.62718617109485 331.002784712987 L70.40470918808083 330.58250265438886 L71.18223220506682 330.15331688116083 L71.95975522205279 329.71634808266236 L72.73727823903879 329.27263561187004 L73.51480125602477 328.8230156608133 L74.29232427301075 328.36800474985563 L75.06984728999674 327.90769818412576 L75.84737030698273 327.4416919233141 L76.62489332396869 326.96903426425274 L77.40241634095469 326.48821108268925 L78.17993935794067 325.997165423695 L78.95746237492666 325.49334930168294 L79.73498539191264 324.97380299113354 L80.51250840889861 324.4352551248082 L81.2900314258846 323.874235748147 L82.0675544428706 323.2871941802391 L82.84507745985657 322.67061406419987 L83.62260047684256 322.02111921206546 L84.40012349382853 321.33556554364435 L85.17764651081453 320.61111632577695 L85.95516952780052 319.845299777039 L86.73269254478649 319.0360496880789 L87.51021556177247 318.1817308604943 L88.28773857875845 317.2811518117151 L89.06526159574445 316.3335673397511 L89.84278461273043 315.3386732735048 L90.62030762971641 314.29659518541604 L91.39783064670239 313.2078721674141 L92.17535366368837 312.0734361121467 L92.95287668067438 310.89458640754884 

`densityPlot` plot for `GroupBy` (i.e. `GroupBy.densityPlot(statDensityArgs)` extensions) works as well:

In [25]:
groupedRangesDF.densityPlot("range", bandWidth = BandWidth.value(10.0))

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M25.484270532552216 343.3019235724016 L25.484270532552216 343.3019235724016 L26.06615690826331 343.2707953177561 L26.648043283974417 343.24045257957334 L27.229929659685524 343.2103082248077 L27.811816035396618 343.1796522298182 L28.39370241110774 343.1476813534692 L28.975588786818832 343.11353267054056 L29.55747516252994 343.07631823614105 L30.139361538241047 343.0351581361378 L30.72124791395214 342.989209426916 L31.303134289663248 342.93768894848614 L31.885020665374356 342.87988865314924 L32.46690704108546 342.8151828573296 L33.04879341679657 342.7430276203354 L33.63067979250768 342.6629532070115 L34.21256616821877 342.5745512378072 L34.79445254392988 342.47745862068905 L35.376338919640986 342.3713406621094 L35.95822529535208 342.2558758522627 L36.54011167106319 342.13074471000823 L37.121998046774294 341.9956247626476 L37.70388442248539 341.8501932410867 L38.285770798196495 341.6941384150359 L38.8676571739076 341.52717970700303 L39.449543549618696 341.3490958488481 L40.0314299253298 341.15975943332603 L40.61331630104091 340.9591753309896 L41.19520267675203 340.7475196675971 L41.777089052463126 340.5251754741048 L42.35897542817423 340.2927608161523 L42.94086180388534 340.051145258513 L43.522748179596434 339.8014509763087 L44.10463455530754 339.5450357093192 L44.68652093101865 339.2834560457272 L45.268407306729756 339.01841114583607 L45.85029368244085 338.7516688551448 L46.43218005815196 338.48497804860045 L47.014066433863064 338.2199728044578 L47.59595280957416 337.9580754275231 L48.177839185285265 337.70040624010016 L48.75972556099637 337.44770828188575 L49.341611936707466 337.20029451052505 L49.92349831241857 336.9580237484879 L50.50538468812968 336.7203095382382 L51.08727106384079 336.4861633897904 L51.66915743955188 336.2542708528887 L52.25104381526299 336.02309569995555 L52.832930190974096 335.7910045792984 L53.41481656668519 335.55640210666115 L53.99670294239631 335.31786479012993 L54.57858931810742 335.07426164490414 L55.160475693818526 334.82484997083094 L55.74236206952962 334.56933654110065 L56.32424844524073 334.3078972654743 L56.906134820951834 334.04115200876197 L57.48802119666293 333.77009533142933 L58.069907572374035 333.49598807779597 L58.65179394808514 333.2202185518885 L59.233680323796236 332.9441451018132 L59.81556669950734 332.6689339618569 L60.39745307521845 332.395406966404 L60.97933945092957 332.12391317138304 L61.561225826640666 331.85423655615836 L62.14311220235177 331.5855490195766 L62.72499857806288 331.31641412073543 L63.306884953773974 331.04484280874874 L63.88877132948508 330.7683981233053 L64.47065770519619 330.4843419000186 L65.0525440809073 330.18981319955867 L65.63443045661839 329.88202573586346 L66.2163168323295 329.5584701508344 L66.7982032080406 329.21710661950755 L67.3800895837517 328.8565339328322 L67.9619759594628 328.4761227874261 L68.54386233517391 328.0761033568828 L69.125748710885 327.65760014341515 L69.70763508659611 327.2226104174223 L70.28952146230722 326.7739260533291 L70.87140783801833 326.3150020782533 L71.45329421372942 325.84977859093016 L72.03518058944053 325.3824657155981 L72.61706696515164 324.9173037700084 L73.19895334086273 324.45831269698226 L73.78083971657384 324.00904589625634 L74.36272609228494 323.572363781245 L74.94461246799604 323.15024159342084 L75.52649884370715 322.74362420729875 L76.10838521941827 322.3523378918336 L76.69027159512937 321.97506538025766 L77.27215797084047 321.60938634646755 L77.85404434655158 321.25188077955795 L78.43593072226268 320.8982881416811 L79.01781709797378 320.54371097891146 L79.59970347368488 320.1828482227516 L80.18158984939599 319.81024112338815 L80.7634762251071 319.4205138632946 L81.34536260081819 319.00859155

... and can be configured the same way:

In [26]:
groupedRangesDF.densityPlot(n = 750, trim = true, adjust = 0.75) { x(range) }.configure {
    alpha = 0.6
    position = Position.stack()
    // can access key column by name as `String`
    fillColor("category") { scale = categoricalColorBrewer(BrewerPalette.Qualitative.Dark2) }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 0.006
 
 
 
 
 
 
 0.007
 
 
 
 
 
 
 0.008
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M19.865713083991892 343.5173045588821 L19.865713083991892 343.5173045588821 L20.396172712402894 343.4950229191171 L20.92663234081388 343.4739138388673 L21.457091969224884 343.4542165663511 L21.987551597635886 343.43614253019837 L22.518011226046887 343.4198624130641 L23.048470854457875 343.4054934896842 L23.578930482868877 343.3930880703843 L24.10939011127988 343.3826238977176 L24.639849739690874 343.3739972762615 L25.17030936810187 343.36701957359185 L25.700768996512878 343.36141752196556 L26.231228624923872 343.35683749073877 L26.761688253334867 343.352853610819 L27.292147881745862 343.3489793403948 L27.82260751015687 343.3446817931165 L28.353067138567866 343.33939793148227 L28.88352676697886 343.3325515805709 L29.413986395389855 343.3235701547132 L29.944446023800865 343.3119000180747 L30.47490565221186 343.29701951636525 L31.005365280622854 343.2784489096527 L31.53582490903385 343.2557566874443 L32.066284537444844 343.2285620342822 L32.59674416585585 343.19653351275684 L33.12720379426685 343.1593843175711 L33.65766342267786 343.116864708595 L34.18812305108885 343.06875243677456 L34.718582679499846 343.0148421235263 L35.24904230791083 342.9549346361493 L35.779501936321836 342.88882751736867 L36.30996156473283 342.81630747805485 L36.84042119314384 342.73714585201554 L37.370880821554834 342.6510977451292 L37.90134044996583 342.55790539319474 L38.43180007837684 342.4573059797669 L38.96225970678783 342.34904386458976 L39.49271933519884 342.23288684538915 L40.02317896360982 342.1086457348912 L40.55363859202082 341.97619619965946 L41.08409822043181 341.83550150089417 L41.61455784884282 341.6866345265176 L42.145017477253816 341.52979733714426 L42.675477105664825 341.36533639318714 L43.20593673407582 341.1937517090345 L43.736396362486815 341.01569840737744 L44.26685599089781 340.83197952532896 L44.797315619308804 340.64352944309206 L45.32777524771981 340.4513879398505 L45.85823487613081 340.25666559015235 L46.3886945045418 340.0605019450869 L46.9191541329528 339.86401863537765 L47.44961376136381 339.66827012416536 L47.9800733897748 339.4741952643031 L48.51053301818581 339.2825730256227 L49.04099264659679 339.0939857135123 L49.571452275007786 338.9087926822226 L50.101911903418795 338.7271169583291 L50.63237153182979 338.5488463598327 L51.1628311602408 338.3736496764299 L51.693290788651794 338.20100733953257 L52.22375041706279 338.0302548457318 L52.75421004547377 337.8606361027839 L53.28466967388478 337.69136294180305 L53.81512930229577 337.52167637373657 L54.34558893070678 337.35090483537687 L54.87604855911778 337.1785147175131 L55.40650818752877 337.00414891081977 L55.93696781593977 336.8276499239286 L56.467427444350776 336.64906526763457 L56.997887072761785 336.4686341723618 L57.528346701172765 336.2867562011455 L58.05880632958376 336.1039438110314 L58.589265957994755 335.9207622727654 L59.119725586405764 335.7377614625779 L59.65018521481676 335.55540479312356 L60.18064484322777 335.37400088695256 L60.71110447163876 335.1936434868013 L61.24156410004976 335.0141645541251 L61.77202372846074 334.8351045804217 L62.30248335687175 334.6557029069487 L62.832942985282756 334.4749094223831 L63.36340261369375 334.2914175017291 L63.893862242104746 334.10371658055544 L64.42432187051574 333.9101614331478 L64.95478149892675 333.70905412887214 L65.48524112733774 333.4987338404031 L66.01570075574875 333.2776692053502 L66.54616038415973 333.04454780722114 L67.07662001257073 332.79835752710784 L67.60707964098172 332.5384549901804 L68.13753926939273 332.2646170450038 L68.66799889780374 331.9770721164844 L69.19845852621474 331.6765093111259 L69.72891815462573 331.3

### Inside `groupBy{}` plot context

We can apply `groupBy` modification to the initial dataset and build a histogram with grouped data the same way:

In [27]:
rangesDF.plot {
    groupBy(category) {
        densityPlot(range)
    }
}

100
 
 
 
 
 
 
 
 
 200
 
 
 
 
 
 
 
 
 300
 
 
 
 
 
 
 
 
 400
 
 
 
 
 
 
 
 
 500
 
 
 
 
 
 
 
 
 600
 
 
 
 
 
 
 
 
 700
 
 
 
 
 
 
 
 
 800
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 0.000
 
 
 
 
 
 
 0.001
 
 
 
 
 
 
 0.002
 
 
 
 
 
 
 0.003
 
 
 
 
 
 
 0.004
 
 
 
 
 
 
 0.005
 
 
 
 
 
 
 
 
 
 
 
 
 <path d="M25.484270532552216 343.28418638518616 L25.484270532552216 343.28418638518616 L26.06615690826331 343.2426481412581 L26.648043283974417 343.19937694811335 L27.229929659685524 343.15407316074266 L27.811816035396618 343.106397210931 L28.39370241110774 343.0559738039986 L28.975588786818832 343.0023970602072 L29.55747516252994 342.94523642588155 L30.139361538241047 342.8840431691673 L30.72124791395214 342.8183572777563 L31.303134289663248 342.74771458944366 L31.885020665374356 342.6716540086075 L32.46690704108546 342.5897246893915 L33.04879341679657 342.5014930957708 L33.63067979250768 342.4065498759211 L34.21256616821877 342.30451650974896 L34.79445254392988 342.195051701076 L35.376338919640986 342.0778574877626 L35.95822529535208 341.9526850332177 L36.54011167106319 341.81934004185274 L37.121998046774294 341.6776877111372 L37.70388442248539 341.5276570973328 L38.285770798196495 341.369244735177 L38.8676571739076 341.2025173188907 L39.449543549618696 341.0276132283298 L40.0314299253298 340.8447426750275 L40.61331630104091 340.6541862526018 L41.19520267675203 340.45629170753074 L41.777089052463126 340.2514688008043 L42.35897542817423 340.04018220756217 L42.94086180388534 339.8229424973528 L43.522748179596434 339.60029534674703 L44.10463455530754 339.37280925142255 L44.68652093101865 339.1410621177205 L45.268407306729756 338.90562721449305 L45.85029368244085 338.6670590451848 L46.43218005815196 338.42587974876557 L47.014066433863064 338.18256664929726 L47.59595280957416 337.9375415430533 L48.177839185285265 337.6911622378292 L48.75972556099637 337.4437167435756 L49.341611936707466 337.1954203626155 L49.92349831241857 336.94641575078384 L50.50538468812968 336.6967758301113 L51.08727106384079 336.4465092434645 L51.66915743955188 336.1955678671404 L52.25104381526299 335.94385575377044 L52.832930190974096 335.6912387783691 L53.41481656668519 335.43755421541726 L53.99670294239631 335.1826194909463 L54.57858931810742 334.92623943236083 L55.160475693818526 334.6682114766373 L55.74236206952962 334.4083284858188 L56.32424844524073 334.1463790439088 L56.906134820951834 333.8821453540695 L57.48802119666293 333.615399099648 L58.069907572374035 333.3458958562358 L58.65179394808514 333.07336882471674 L59.233680323796236 332.79752277956266 L59.81556669950734 332.51802917901557 L60.39745307521845 332.2345233560981 L60.97933945092957 331.9466045996518 L61.561225826640666 331.65383974743366 L62.14311220235177 331.3557706597423 L62.72499857806288 331.05192563888374 L63.306884953773974 330.7418345284188 L63.88877132948508 330.4250468909809 L64.47065770519619 330.1011523501767 L65.0525440809073 329.7698019156166 L65.63443045661839 329.4307289127568 L66.2163168323295 329.0837680288514 L66.7982032080406 328.7288709749903 L67.3800895837517 328.3661173571132 L67.9619759594628 327.99571954389 L68.54386233517391 327.6180206069106 L69.125748710885 327.2334847723922 L69.70763508659611 326.8426802415309 L70.28952146230722 326.44625468233335 L70.87140783801833 326.0449041404755 L71.45329421372942 325.6393365311453 L72.03518058944053 325.23023123025666 L72.61706696515164 324.81819655767896 L73.19895334086273 324.4037271183305 L73.78083971657384 323.98716302683096 L74.36272609228494 323.5686529831888 L74.94461246799604 323.1481229938915 L75.52649884370715 322.7252522556925 L76.10838521941827 322.29945735629326 L76.69027159512937 321.869885520616 L77.27215797084047 321.43541717118467 L77.85404434655158 320.99467760599356 L78.43593072226268 320.54605715678093 L79.01781709797378 320.0877388022165 L79.59970347368488 319.61773189728734 L80.18158984939599 319.1339104593836 L80.7634762251071 318.6340543334646 L81.34536260081819 318.1158915457635 L81.9